### Sentiment analysis on twitter dataset

Возьмем модель `sentiment-roberta-large-english` и дообучим ее на датасете твитов `carblacac/twitter-sentiment-analysis`.

In [2]:
#!streamlit run /home/theodore/anaconda3/envs/ds/lib/python3.10/site-packages/ipykernel_launcher.py

In [3]:
!pip install transformers datasets

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [1]:
# import json

# with open("arxivData.json", 'r') as f:
#     arxiv_data = json.load(f)

# arxiv_data[0]['tag']

In [1]:
from datasets import load_dataset
import transformers
import pandas as pd
import numpy as np

In [2]:
data = load_dataset("carblacac/twitter-sentiment-analysis")

Found cached dataset twitter-sentiment-analysis (/home/theodore/.cache/huggingface/datasets/carblacac___twitter-sentiment-analysis/default/1.0.0/cd65e23e456de6a4f7264e305380b0ffe804d6f5bfd361c0ec0f68d8d1fab95b)


  0%|          | 0/3 [00:00<?, ?it/s]

In [3]:
data

DatasetDict({
    train: Dataset({
        features: ['text', 'feeling'],
        num_rows: 119988
    })
    validation: Dataset({
        features: ['text', 'feeling'],
        num_rows: 29997
    })
    test: Dataset({
        features: ['text', 'feeling'],
        num_rows: 61998
    })
})

In [4]:
# tweets_df = pd.read_csv("twitter_sentiment.csv", names=["target", "ids", "date", "flag", "user", "text"],
#                          encoding='utf-8', encoding_errors='ignore')
# tweets_df.head()
# #tweets_df.shape

In [5]:
from transformers import AutoModelForSequenceClassification, AutoTokenizer, AutoModel, Trainer, TrainingArguments, LineByLineTextDataset
from transformers import pipeline

# classifier = pipeline('sentiment-analysis', model="siebert/sentiment-roberta-large-english")


# print("Preparing the training data...")
# # dataset = LineByLineTextDataset(
# #     file_path=<MAKE_YOUR_DATA_HERE>, tokenizer=tokenizer, block_size=128)

tokenizer = AutoTokenizer.from_pretrained("siebert/sentiment-roberta-large-english")
model = AutoModelForSequenceClassification.from_pretrained("siebert/sentiment-roberta-large-english", num_labels=2)

# print("Dataset ready!")
dataset = data.map(lambda xs: tokenizer(xs["text"], truncation=True, padding='max_length'))

Loading cached processed dataset at /home/theodore/.cache/huggingface/datasets/carblacac___twitter-sentiment-analysis/default/1.0.0/cd65e23e456de6a4f7264e305380b0ffe804d6f5bfd361c0ec0f68d8d1fab95b/cache-798641a24e025595.arrow
Loading cached processed dataset at /home/theodore/.cache/huggingface/datasets/carblacac___twitter-sentiment-analysis/default/1.0.0/cd65e23e456de6a4f7264e305380b0ffe804d6f5bfd361c0ec0f68d8d1fab95b/cache-5ac250acc1a0a444.arrow
Loading cached processed dataset at /home/theodore/.cache/huggingface/datasets/carblacac___twitter-sentiment-analysis/default/1.0.0/cd65e23e456de6a4f7264e305380b0ffe804d6f5bfd361c0ec0f68d8d1fab95b/cache-6ee382dff31af9fb.arrow


In [10]:
# model.to('cpu');

In [7]:
from datasets import ClassLabel

dataset = dataset.rename_column("feeling", "labels")
dataset = dataset.cast_column("labels", ClassLabel(names=['0', '1']))
dataset = dataset.align_labels_with_mapping({'0': 1, '1': 0}, "labels")

In [13]:
trainer = Trainer(
    model=model, train_dataset=dataset["train"].shuffle().select(range(10000)),
    eval_dataset = dataset['test'].select(range(5000)),
    args=TrainingArguments(
        output_dir="./my_saved_model", overwrite_output_dir=True,
        num_train_epochs=1, per_device_train_batch_size=4,
        save_steps=10_000, save_total_limit=2),
)

trainer.train()

/usr/local/lib/python3.9/dist-packages/transformers/optimization.py:391: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  warnings.warn(


TrainOutput(global_step=2500, training_loss=0.7088180541992187, metrics={'train_runtime': 3241.3296, 'train_samples_per_second': 3.085, 'train_steps_per_second': 0.771, 'total_flos': 9319313633280000.0, 'train_loss': 0.7088180541992187, 'epoch': 1.0})

In [14]:
import torch
torch.save(model.state_dict(), "./model_cached.pth")

In [ ]:
import pandas as pd
df = pd.read_json("./arxivData.json")
df.loc[0]

In [18]:
from google.colab import drive
drive.mount('/content/gdrive')

Mounted at /content/gdrive


In [19]:
model_save_name = 'model_cached.pth'
path = F"/content/gdrive/My Drive/cached_model.pth" 
torch.save(model.state_dict(), path)

In [6]:
import numpy as np
import torch
from transformers import AutoModelForSequenceClassification, AutoTokenizer, AutoModel, Trainer, TrainingArguments, LineByLineTextDataset
import evaluate


model_enhanced = AutoModelForSequenceClassification.from_pretrained("siebert/sentiment-roberta-large-english", num_labels=2)
model_enhanced.load_state_dict(torch.load('model_cached_2.pth', map_location=torch.device('cpu')))

metric = evaluate.load("accuracy")

def compute_metrics(eval_pred):
    logits, labels = eval_pred
    predictions = np.argmax(logits, axis=-1)
    return metric.compute(predictions=predictions, references=labels)


In [8]:
task_evaluator = evaluate.evaluator("text-classification")
data_to_evaluate = dataset["test"].select(range(500))
data_to_evaluate = data_to_evaluate.rename_column("feeling", "label")

results = task_evaluator.compute(
    model_or_pipeline=model_enhanced,
    tokenizer=tokenizer,
    data=data_to_evaluate,
    label_mapping={"POSITIVE": 1.0, "NEGATIVE": 0.0},
    metric="accuracy",
    strategy="simple"
)

In [9]:
results

{'accuracy': 0.758,
 'total_time_in_seconds': 123.58850028699817,
 'samples_per_second': 4.045683852776724,
 'latency_in_seconds': 0.2471770005739963}